In [ ]:
# 
# CL-Metrics-Avalanche-DatasetB-2classes.ipynb
# 
# Author(s):
# Lan Mei <lanmei@student.ethz.ch>
#
# ======================================================================
# 
# Copyright (c) 2024 ETH Zurich.
# 
# Licensed under the Apache License, Version 2.0 (the "License");
# you may not use this file except in compliance with the License.
# You may obtain a copy of the License at
# 
# http://www.apache.org/licenses/LICENSE-2.0
# 
# Unless required by applicable law or agreed to in writing, software
# distributed under the License is distributed on an "AS IS" BASIS,
# WITHOUT WARRANTIES OR CONDITIONS OF ANY KIND, either express or implied.
# See the License for the specific language governing permissions and
# limitations under the License.
# SPDX-License-Identifier: Apache-2.0

In [1]:
import numpy as np

from pyexpat import model
import torch
import torch.nn as nn
import torch.optim as optim
import torch as t
import torch.nn.functional as F
import json
import random
from torchvision.transforms import Compose

import os
from os import path, walk
import pandas as pd
from scipy import signal

CUR_FOLDER = os.path.abspath("")

# Dataset B downloaded from the link in README.md and put into the "data" folder. Note that binary files should be converted to csv files.
DATASET_1_PATH = CUR_FOLDER + "/data/DatasetB/SubjectA_1129_S1/MM/csv/" 
DATASET_2_PATH = CUR_FOLDER + "/data/DatasetB/SubjectA_1206_S2/MM/csv/" 
DATASET_3_PATH = CUR_FOLDER + "/data/DatasetB/SubjectA_1213_S3/MM/csv/" 
DATASET_4_PATH = CUR_FOLDER + "/data/DatasetB/SubjectA_1220_S4/MM/csv/" 
CONFIG_PATH = CUR_FOLDER + "/config_avalanche.json"

with open(CONFIG_PATH) as fp:
    config = json.load(fp)

In [2]:
# filters
def notch_multiEEG(data,fs):
    '''
    50Hz multi channel EEG
    
    Params
    ------
    data: np array (n_ch,n_s)
        EEG data
    fs: float
        sampling frequency
    
    Return
    ------
    data_filt: np array (n_ch, n_s)
        filtered EEG data 
    '''
    
    w0 = 50/(fs/2)
    Q = 30
    notch_filter_50Hz = signal.iirnotch(w0, Q)

    
    data_filt = np.zeros(data.shape)
    for chan in range(data.shape[0]):
         
        data_filt[chan, :]= signal.lfilter(*notch_filter_50Hz, data[chan, :])
        
    return data_filt

    
def bandpass_multiEEG(data, fs, f_low, f_high, order):
    '''
    Bandpass multi channel EEG
    
    Params
    ------
    data: np array (n_ch,n_s)
        EEG data
    f_low: float
        lower corner frequency [Hz]
    f_high: float
        upper corner_frequency [Hz]
    fs: float
        sampling frequency
    
    Return
    ------
    data_filt: np array (n_ch, n_s)
        filtered EEG data 
    '''

    nyq = 0.5 * fs
    low_freq = f_low / nyq
    high_freq = f_high / nyq
    filt_coef = signal.butter(N=order, Wn=[low_freq, high_freq], btype='bandpass', output='sos')
    
    for chan in range(data.shape[0]):
        data[chan, :] = signal.sosfilt(filt_coef, data[chan, :])
    return data


In [3]:
def get_data(directory, n_files, fs, filter_config, ds=1):
    '''
    Preprocess and obtain the data
    
    Params
    ------
    directory: string
        location of the csv files of data
    n_files: int
        number of files in the directory
    fs: int
        sampling frequency [Hz]
    filter_config: dictionary
        configuration of filter
    ds: int
        downsampling rate
    
    Return
    ------
    data_filt: np array 
        data and labels
    '''
    
    intertrial_sec = 4  # at least 4 seconds between trials
    samples_stimulus = 1950 # stimulus is 2000 samples, but some are lost due to transmission errors
    offset_sec = -5  # startpoint for the stimulus to load. choose time window (0,samples_sec) for classification in config file: t1_factor, t2_factor
    offset = int(fs * offset_sec)  # number of samples how much later than the stimulus a trial starts
    samples = samples_stimulus - offset  # number of samples of trial before cut
    intertrial = int(fs * intertrial_sec)  # number of samples in between trials
    number_of_trials = 20

    # trigger values
    trigger_tongue = 70
    trigger_nothing = 100

    # labels for classifier
    lb_nothing = 0
    lb_left = 1
    lb_right = 2
    lb_tongue = 3

    N_ch = 8

    number_of_runs = n_files

    file_index = 0
    runs = np.zeros((number_of_runs, number_of_trials, N_ch, samples), dtype=np.float32)
    y_runs = np.zeros((number_of_runs, number_of_trials), dtype=np.float32)

    preprocess_mean = 0
    
    valid_trials = 0
    
    for root, dirs, files in walk(directory):
        for file in files:
            print(file)
            file_path = path.join(root, file)
            df = pd.read_csv(file_path,sep=',')
            data = df.to_numpy(dtype=np.float32)
            X = np.transpose(data[:,:]) # X: [channels+triggers, samples]
            temp_afterfilt_X = X[:-1,:].copy()
            
            # Filtering
            temp_afterfilt_X = notch_multiEEG(temp_afterfilt_X, fs)
            temp_afterfilt_X = bandpass_multiEEG(temp_afterfilt_X, fs, filter_config['fc_low'], filter_config['fc_high'],
                                              filter_config['order'])
            
            # Subtracting moving avg.
            N = int(250/2)
            for i in range(N_ch):
                temp_afterfilt_X_moving_avg = np.convolve(temp_afterfilt_X[i], np.ones(N)/N, mode='same')
                temp_afterfilt_X[i] = temp_afterfilt_X[i] - temp_afterfilt_X_moving_avg
            
            trials = np.zeros((number_of_trials, N_ch, samples), dtype=np.float32)
            y = np.zeros(number_of_trials, dtype=np.float32) # to store the labels
            
            n_samples=X.shape[1] # number of samples in the run
            k = 0 # trial
            sample = 0
            
            while sample < n_samples:
                # two class classification
                if X[-1, sample] == trigger_nothing:  # rest
                    start_trial = sample + offset
                    stop_trial = start_trial + samples
                    temp_filt = temp_afterfilt_X[0:N_ch, start_trial:stop_trial]

                    trials[k] = temp_filt
                    y[k] = lb_left
                    y[k] = y[k] - 1
                    sample = sample + samples_stimulus + intertrial  # skip to the next sample
                    k += 1  # go to the next trial
                    valid_trials += 1
                    
                    ## Needed only for downsampling 
                    # if ds > 1:
                    #     samples_ds = int(np.ceil(samples / ds))
                    #     X_ds = np.zeros((N_ch, samples_ds), dtype=np.float64)
                    #     for chan in range(N_ch):
                    #         X_ds[chan] = signal.decimate(trial[chan, :], ds)
                    #     trial = X_ds

                elif X[-1, sample] == trigger_tongue:  # tongue MM
                    start_trial = sample + offset  
                    stop_trial = start_trial + samples  
                    temp_filt = temp_afterfilt_X[0:N_ch, start_trial:stop_trial]  

                    trials[k] = temp_filt
                    y[k] = lb_right
                    y[k] = y[k] - 1 
                    sample = sample + samples_stimulus + intertrial  # skip to the next sample
                    k += 1  # go to the next trial
                    valid_trials += 1

                    ## Needed only for downsampling 
                    # if ds > 1:
                    #     samples_ds = int(np.ceil(samples / ds))
                    #     X_ds = np.zeros((N_ch, samples_ds), dtype=np.float64)
                    #     for chan in range(N_ch):
                    #         X_ds[chan] = signal.decimate(trial[chan, :], ds)
                    #     trial = X_ds

                else:
                    sample += 1  # go to the next sample

            runs[file_index] = trials
            y_runs[file_index] = y
            file_index += 1

    X = runs.reshape(number_of_runs * number_of_trials, N_ch, samples)
    y = y_runs.reshape(number_of_runs * number_of_trials)


    if ds > 1:
        samples_ds = int(np.ceil(samples / ds))
        X_ds = np.zeros((number_of_runs * number_of_trials, N_ch, samples_ds), dtype=np.float32)
        for trial in range(number_of_runs * number_of_trials):
            for chan in range(N_ch):
                X_ds[trial, chan] = signal.decimate(X[trial, chan, :], ds)
        X = X_ds

    if valid_trials != number_of_runs * number_of_trials:
        X_new_shape = np.zeros((valid_trials, N_ch, samples))
        y_new_shape = np.zeros((valid_trials))
        new_trial_idx = 0
        for trial_idx in range(number_of_runs * number_of_trials):
            if np.any(X[trial_idx]):
                X_new_shape[new_trial_idx] = X[trial_idx]
                y_new_shape[new_trial_idx] = y[trial_idx]
                new_trial_idx += 1
                
        X = X_new_shape
        y = y_new_shape
        
    #print(X.shape)
                
    return X,y


In [4]:
class BCI_Drone(t.utils.data.Dataset):

    def __init__(self, root, fs=500, transform=None, filter_config=None, ds=1):
        self.root = root
        self.fs = fs
        self.transform = transform
        self.filter_config = filter_config
        self.ds = ds
        self.samples, self.labels = self._load_data()

    def __len__(self):  
        return len(self.samples)

    def __getitem__(self, idx):  
        
        sample = self.samples[idx, :, :]
        label = self.labels[idx]

        if self.transform:
            sample = self.transform(sample)
        return sample, label

    def _load_data(self):
        n_files = len(os.listdir(self.root))
        X, y = get_data(self.root, n_files, self.fs, self.filter_config, self.ds)
        
        data_return = t.Tensor(X).to(dtype=t.float)
        class_return = t.Tensor(y).to(dtype=t.long)

        return data_return, class_return

In [5]:
class Identity(object):

    def __call__(self, sample):
        return sample


class TimeWindowPostCue(object):

    def __init__(self, fs, t1_factor, t2_factor):
        self.t1 = int(t1_factor * fs)
        self.t2 = int(t2_factor * fs)

    def __call__(self, sample):
        return sample[:, :, self.t1:self.t2]


class ReshapeTensor(object):
    def __call__(self, sample):
        return sample.view(1, sample.shape[0], sample.shape[1])
    
class ReshapeFinal(object):
    def __call__(self, sample):
        return sample.view(1, -1)

class PaddingTensor(object):
    def __init__(self, padding):
        self.padding = int(padding)

    def __call__(self, sample):
        if self.padding == 0:
            return sample

        sample_pad = np.zeros((sample.shape[0], sample.shape[1], sample.shape[2] + self.padding), dtype=np.float32)
        for i in range(sample_pad.shape[0]):
            for ch in range(sample_pad.shape[1]):
                for j in range(sample.shape[2]):
                    sample_pad[i, ch, j] = sample[i, ch, j]

        return sample_pad

def get_transform(fs, t1_factor, t2_factor, filter_config, padding=0):

    if filter_config is None:
        filter_config = {'type': None}
    elif 'type' not in filter_config:
        filter_config['type'] = 'none'

    if padding is None:
        padding = 0

    return Compose([ReshapeTensor(),
                    TimeWindowPostCue(fs, t1_factor, t2_factor),
                    PaddingTensor(padding)])

def load_data(dir_data, data_config):
    try:
        padding = data_config['padding']
    except:
        padding = 0
    transform      = get_transform(data_config['fs'], data_config['t1_factor'],
                                   data_config['t2_factor'], data_config['filter'], padding)
    loaded_data  = BCI_Drone(root=dir_data, fs=data_config['fs'], transform=transform, filter_config = data_config['filter'], ds = data_config['ds'])
    return loaded_data


In [6]:
manualSeed = 4
torch.manual_seed(manualSeed)
random.seed(manualSeed)
np.random.seed(manualSeed)
# using GPU
torch.cuda.manual_seed(manualSeed)
torch.cuda.manual_seed_all(manualSeed)
# using cudnn
torch.backends.cudnn.enabled = False 
torch.backends.cudnn.benchmark = False
torch.backends.cudnn.deterministic = True
# dataloader number of workers 0, if > 0 background processes with their own seeds are started
nb_workers = 0
def _init_fn():
    np.random.seed(manualSeed)
    

In [7]:
dataset_1129_MM_A = load_data(DATASET_1_PATH, config['treat']['data'])
dataset_1206_MM_A = load_data(DATASET_2_PATH, config['treat']['data'])
dataset_1213_MM_A = load_data(DATASET_3_PATH, config['treat']['data'])
dataset_1220_MM_A = load_data(DATASET_4_PATH, config['treat']['data'])

Data_20231129_114031_A_S1_MM_1.csv
Data_20231129_115426_A_S1_MM_2.csv
Data_20231129_121012_A_S1_MM_3.csv
Data_20231129_122414_A_S1_MM_4.csv
Data_20231129_123859_A_S1_MM_5.csv
100
(100, 8, 4450)
Data_20231206_111947_MM_1_2.csv
Data_20231206_113703_MM_2_2.csv
Data_20231206_115349_MM_3_2.csv
Data_20231206_121643_MM_4_2.csv
Data_20231206_123226_MM_5_2.csv
100
(100, 8, 4450)
Data_20231213_103954_MM_1_2.csv
Data_20231213_110021_MM_2_2.csv
Data_20231213_111803_MM_3_2.csv
Data_20231213_113815_MM_4_2.csv
Data_20231213_115714_MM_5_2.csv
100
(100, 8, 4450)
Data_20231220_103456_MM_1_2.csv
Data_20231220_105828_MM_2_2.csv
Data_20231220_111706_MM_3_2.csv
Data_20231220_114136_MM_4_2.csv
Data_20231220_115909_MM_5_2.csv
100
(100, 8, 4450)


In [12]:
from avalanche.benchmarks.utils import AvalancheDataset

from avalanche.benchmarks.utils import make_classification_dataset

#train on all data, test on last 2 runs in S1
train_size_1129 = int(0.6 * len(dataset_1129_MM_A.labels))
test_size_1129 = len(dataset_1129_MM_A.labels) - train_size_1129
test_dataset_1129 = torch.utils.data.Subset(dataset_1129_MM_A, list(range(train_size_1129, train_size_1129+test_size_1129)))

test_dataset_1129.targets = dataset_1129_MM_A.labels[test_dataset_1129.indices]

avalanche_test_dataset_1129 = make_classification_dataset(test_dataset_1129, task_labels=0)

dataset_1129_MM_A.targets = dataset_1129_MM_A.labels

avalanche_train_dataset_1129_full_pretrained = make_classification_dataset(dataset_1129_MM_A, task_labels=0)

# t3v2 in S2
train_size_1206 = int(0.6 * len(dataset_1206_MM_A.labels))
test_size_1206 = len(dataset_1206_MM_A.labels) - train_size_1206
train_dataset_1206 = torch.utils.data.Subset(dataset_1206_MM_A, list(range(0, train_size_1206)))
test_dataset_1206 = torch.utils.data.Subset(dataset_1206_MM_A, list(range(train_size_1206, train_size_1206+test_size_1206)))

train_dataset_1206.targets = dataset_1206_MM_A.labels[train_dataset_1206.indices]
test_dataset_1206.targets = dataset_1206_MM_A.labels[test_dataset_1206.indices]

avalanche_train_dataset_1206 = make_classification_dataset(train_dataset_1206, task_labels=0)
avalanche_test_dataset_1206 = make_classification_dataset(test_dataset_1206, task_labels=0)

# t3v2 in S3
train_size_1213 = int(0.6 * len(dataset_1213_MM_A.labels))
test_size_1213 = len(dataset_1213_MM_A.labels) - train_size_1213
train_dataset_1213 = torch.utils.data.Subset(dataset_1213_MM_A, list(range(0, train_size_1213)))
test_dataset_1213 = torch.utils.data.Subset(dataset_1213_MM_A, list(range(train_size_1213, train_size_1213+test_size_1213)))

train_dataset_1213.targets = dataset_1213_MM_A.labels[train_dataset_1213.indices]
test_dataset_1213.targets = dataset_1213_MM_A.labels[test_dataset_1213.indices]

avalanche_train_dataset_1213 = make_classification_dataset(train_dataset_1213, task_labels=0)
avalanche_test_dataset_1213 = make_classification_dataset(test_dataset_1213, task_labels=0)

# t3v2 in S4
train_size_1220 = int(0.6 * len(dataset_1220_MM_A.labels))
test_size_1220 = len(dataset_1220_MM_A.labels) - train_size_1220
train_dataset_1220 = torch.utils.data.Subset(dataset_1220_MM_A, list(range(0, train_size_1220)))
test_dataset_1220 = torch.utils.data.Subset(dataset_1220_MM_A, list(range(train_size_1220, train_size_1220+test_size_1220)))

train_dataset_1220.targets = dataset_1220_MM_A.labels[train_dataset_1220.indices]
test_dataset_1220.targets = dataset_1220_MM_A.labels[test_dataset_1220.indices]

avalanche_train_dataset_1220 = make_classification_dataset(train_dataset_1220, task_labels=0)
avalanche_test_dataset_1220 = make_classification_dataset(test_dataset_1220, task_labels=0)

dataset_1129_MM_A.targets = dataset_1129_MM_A.labels

avalanche_train_dataset_1129_full_pretrained = make_classification_dataset(dataset_1129_MM_A, task_labels=0)

In [15]:
from avalanche.benchmarks.generators import nc_benchmark, ni_benchmark, dataset_benchmark

scenario = dataset_benchmark(
    [avalanche_train_dataset_1129_full_pretrained, avalanche_train_dataset_1206, avalanche_train_dataset_1213, avalanche_train_dataset_1220], [avalanche_test_dataset_1129, avalanche_test_dataset_1206, avalanche_test_dataset_1213, avalanche_test_dataset_1220]
)

train_stream = scenario.train_stream

for experience in train_stream:
    task = experience.task_label
    exp_id = experience.current_experience
    training_dataset = experience.dataset
    print('Task {} batch {} -> train'.format(task, exp_id))
    print('This batch contains', len(training_dataset), 'patterns')
    
test_stream = scenario.test_stream

for experience in test_stream:
    task = experience.task_label
    exp_id = experience.current_experience
    test_dataset = experience.dataset
    print('Task {} batch {} -> test'.format(task, exp_id))
    print('This batch contains', len(test_dataset), 'patterns')

Task 0 batch 0 -> train
This batch contains 100 patterns
Task 0 batch 1 -> train
This batch contains 60 patterns
Task 0 batch 2 -> train
This batch contains 60 patterns
Task 0 batch 3 -> train
This batch contains 60 patterns
Task 0 batch 0 -> test
This batch contains 40 patterns
Task 0 batch 1 -> test
This batch contains 40 patterns
Task 0 batch 2 -> test
This batch contains 40 patterns
Task 0 batch 3 -> test
This batch contains 40 patterns


## MI-BMINet

In [8]:
class edgeEEGNetBaseline(t.nn.Module):

    def __init__(self, F1=8, D=2, F2=None, C=8, T=2000, N=4, Nf=64, Nf2=16, p_dropout=0.5, activation='relu', # C=8
                 dropout_type='TimeDropout2D'):
        """
        F1:           Number of spectral filters
        D:            Number of spacial filters (per spectral filter), F2 = F1 * D
        F2:           Number or None. If None, then F2 = F1 * D
        C:            Number of EEG channels
        T:            Number of time samples
        N:            Number of classes
	    Nf:           Size of temporal filter
        p_dropout:    Dropout Probability
        activation:   string, either 'elu' or 'relu'
        dropout_type: string, either 'dropout', 'SpatialDropout2d' or 'TimeDropout2D'
        """
        super(edgeEEGNetBaseline, self).__init__()

        # prepare network constants
        if F2 is None:
            F2 = F1 * D

        # check the activation input
        activation = activation.lower()
        assert activation in ['elu', 'relu']
        print("activation relu?: ", activation)

        # Prepare Dropout Type
        if dropout_type.lower() == 'dropout':
            dropout = t.nn.Dropout
        elif dropout_type.lower() == 'spatialdropout2d':
            dropout = t.nn.Dropout2d
        elif dropout_type.lower() == 'timedropout2d':
            dropout = TimeDropout2d
        else:
            raise ValueError("dropout_type must be one of SpatialDropout2d, Dropout or "
                             "WrongDropout2d")

        # store local values
        self.F1, self.D, self.F2, self.C, self.T, self.N = (F1, D, F2, C, T, N)
        self.p_dropout, self.activation = (p_dropout, activation)

        # Number of input neurons to the final fully connected layer
        n_features = (T // 8) // 8

        # Block 1
        self.conv1 = t.nn.Conv2d(1, F1, (C, 1), bias=False)
        self.batch_norm1 = t.nn.BatchNorm2d(F1, momentum=0.01, eps=0.001)
        self.conv2_pad = t.nn.ZeroPad2d((Nf//2-1, Nf//2, 0, 0)) 
        self.conv2 = t.nn.Conv2d(F1, D * F1, (1, Nf), groups=F1, bias=False)
        self.batch_norm2 = t.nn.BatchNorm2d(D * F1, momentum=0.01, eps=0.001)
        self.activation1 = t.nn.ELU(inplace=True) if activation == 'elu' else t.nn.ReLU(inplace=True)
        self.pool1 = t.nn.AvgPool2d((1, 8))
        self.dropout1 = t.nn.Dropout(p=p_dropout)

        # Block 2
        self.sep_conv_pad = t.nn.ZeroPad2d((7, 8, 0, 0))
        self.sep_conv1 = t.nn.Conv2d(D * F1, D * F1, (1, 16), groups=D * F1, bias=False)
        self.sep_conv2 = t.nn.Conv2d(D * F1, F2, (1, 1), bias=False)
        self.batch_norm3 = t.nn.BatchNorm2d(F2, momentum=0.01, eps=0.001)
        self.activation2 = t.nn.ELU(inplace=True) if activation == 'elu' else t.nn.ReLU(inplace=True)
        self.pool2 = t.nn.AvgPool2d((1, 8))
        self.dropout2 = dropout(p=p_dropout)

        # Fully connected layer (classifier)
        self.flatten = t.nn.Flatten()
        self.fc = t.nn.Linear(F2 * n_features, N, bias=True)

        # initialize weights
        self._initialize_params()

    def forward(self, x, with_stats=False):

        # input dimensions: (s, 1, C, T) [batchsize, 1, numb of Channels, T]

        # Block 1
        
        x = self.conv1(x)            # output dim: (s, F1, C, T-1) [batchsize, F1, 1, T]
        x = self.batch_norm1(x)      #[batchsize, F1, 1, T]
        x = self.conv2_pad(x)        
        x = self.conv2(x)            
        
        x = self.batch_norm2(x)
        x = self.activation1(x)
        x = self.pool1(x)            # output dim: (s, D * F1, 1, T // 8)
        x = self.dropout1(x)

        # Block2
        x = self.sep_conv_pad(x)
        x = self.sep_conv1(x)        # output dim: (s, D * F1, 1, T // 8 - 1)
        x = self.sep_conv2(x)        # output dim: (s, F2, 1, T // 8 - 1)
        
        x = self.batch_norm3(x)
        x = self.activation2(x)
        x = self.pool2(x)            # output dim: (s, F2, 1, T // 64)
        x = self.dropout2(x)
        

        # Classification
        x = self.flatten(x)          # output dim: (s, F2 * (T // 64))
        x = self.fc(x)               # output dim: (s, N)
        
        ## Only if we need to store weights of the network
        #if with_stats:
        #    stats = [('conv1_w', self.conv1.weight.data),
        #             ('conv2_w', self.conv2.weight.data),
        #             ('sep_conv1_w', self.sep_conv1.weight.data),
        #             ('sep_conv2_w', self.sep_conv2.weight.data),
        #             ('fc_w', self.fc.weight.data),
        #             ('fc_b', self.fc.bias.data)]
        #    return stats, x
        return x

    def forward_with_tensor_stats(self, x):
        return self.forward(x, with_stats=True)

    def _initialize_params(self, weight_init=t.nn.init.xavier_uniform_, bias_init=t.nn.init.zeros_):
        """
        Initializes all the parameters of the model

        Parameters:
         - weight_init: t.nn.init inplace function
         - bias_init:   t.nn.init inplace function

        """
        def init_weight(m):
            if isinstance(m, t.nn.Conv2d) or isinstance(m, t.nn.Linear):
                weight_init(m.weight)
            if isinstance(m, t.nn.Linear):
                bias_init(m.bias)

        self.apply(init_weight)

class Flatten(t.nn.Module):
    def forward(self, input):
        return input.view(input.size(0), -1)

class TimeDropout2d(t.nn.Dropout2d):
    """
    Dropout layer, where the last dimension is treated as channels
    """
    def __init__(self, p=0.5, inplace=False):
        """
        See t.nn.Dropout2d for parameters
        """
        super(TimeDropout2d, self).__init__(p=p, inplace=inplace)

    def forward(self, input):
        if self.training:
            input = input.permute(0, 3, 1, 2)
            input = F.dropout2d(input, self.p, True, self.inplace)
            input = input.permute(0, 2, 3, 1)
        return input

In [9]:
from avalanche.training.supervised import Naive, CWRStar, Replay, GDumb, Cumulative, LwF, GEM, AGEM, EWC  # and many more!

C:\Users\bci-admin\anaconda3\envs\avalanche\lib\site-packages\torchaudio\backend\utils.py:62: UserWarning: No audio backend is available.
  warnings.warn("No audio backend is available.")


In [10]:
manualSeed = 4
torch.manual_seed(manualSeed)
random.seed(manualSeed)
np.random.seed(manualSeed)

In [11]:
# Not used yet, change network initialization seeds
from avalanche.training.utils import get_last_fc_layer, freeze_up_to
from avalanche.core import SupervisedPlugin

## Naive TL

In [ ]:
class ModifyEpochsP(SupervisedPlugin):

    def __init__(self):
        super().__init__()

    def after_training_exp(self, strategy, **kwargs):
        """
        Train epochs fixed as 100.
        """
        strategy.train_epochs = 50


full_results = []

for manualSeed in range(5):
    
    print('Rand Seed: {}'.format(manualSeed))
    
    os.environ['PYTHONHASHSEED'] = str(manualSeed)
    torch.manual_seed(manualSeed)
    random.seed(manualSeed)
    np.random.seed(manualSeed)
    torch.backends.cudnn.deterministic = True
    
    model = edgeEEGNetBaseline(**config['indiv']['net']['params'])

    loss_fn = torch.nn.modules.loss.CrossEntropyLoss(**config['indiv']['loss_function']['params'])

    optimizer = optim.Adam(model.parameters(), lr=1e-3, eps=1e-7)

    cl_strategy = Naive(
        model, optimizer, loss_fn, train_mb_size=10, eval_mb_size=10,
        train_epochs=40, plugins=[ModifyEpochsP()]
    )

    # TRAINING LOOP
    print('Starting experiment...')
    results = []
    for experience in scenario.train_stream:
        print("Start of experience: ", experience.current_experience)
        print("Current Classes: ", experience.classes_in_this_experience)

        cl_strategy.train(experience)
        print('Training completed')

        print('Computing accuracy on the whole test set')
        results.append(cl_strategy.eval(scenario.test_stream))
        
    full_results.append(results)

In [18]:
#Accuracy
exp_val = np.zeros((4,4,5))

for item_no in range(len(full_results)):

    exp_val[0,0,item_no] = (full_results[item_no][0]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000'])
    exp_val[0,1,item_no] = (full_results[item_no][0]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001'])
    exp_val[0,2,item_no] = (full_results[item_no][0]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp002'])
    exp_val[0,3,item_no] = (full_results[item_no][0]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp003'])
    exp_val[1,0,item_no] = (full_results[item_no][1]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000'])
    exp_val[1,1,item_no] = (full_results[item_no][1]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001'])
    exp_val[1,2,item_no] = (full_results[item_no][1]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp002'])
    exp_val[1,3,item_no] = (full_results[item_no][1]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp003'])
    exp_val[2,0,item_no] = (full_results[item_no][2]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000'])
    exp_val[2,1,item_no] = (full_results[item_no][2]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001'])
    exp_val[2,2,item_no] = (full_results[item_no][2]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp002'])
    exp_val[2,3,item_no] = (full_results[item_no][2]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp003'])
    exp_val[3,0,item_no] = (full_results[item_no][3]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000'])
    exp_val[3,1,item_no] = (full_results[item_no][3]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001'])
    exp_val[3,2,item_no] = (full_results[item_no][3]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp002'])
    exp_val[3,3,item_no] = (full_results[item_no][3]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp003'])
    
for i in range(4):
    for j in range(4):
        print("Avg. ± Std. for exp {} val {}: {:.2f}±{:.2f}% ".format(i, j, np.array(exp_val[i,j]).mean()*100, np.array(exp_val[i,j]).std()*100))
        #print("Std. for exp {} val {}: {}".format(i, j, np.array(exp_val[i,j]).std()))

Avg. ± Std. for exp 0 val 0: 100.00±0.00% 
Avg. ± Std. for exp 0 val 1: 70.00±2.74% 
Avg. ± Std. for exp 0 val 2: 69.00±3.74% 
Avg. ± Std. for exp 0 val 3: 64.50±4.00% 
Avg. ± Std. for exp 1 val 0: 89.50±8.12% 
Avg. ± Std. for exp 1 val 1: 82.50±6.32% 
Avg. ± Std. for exp 1 val 2: 85.00±10.12% 
Avg. ± Std. for exp 1 val 3: 84.00±5.15% 
Avg. ± Std. for exp 2 val 0: 73.00±4.00% 
Avg. ± Std. for exp 2 val 1: 83.50±2.55% 
Avg. ± Std. for exp 2 val 2: 89.50±1.87% 
Avg. ± Std. for exp 2 val 3: 82.50±6.89% 
Avg. ± Std. for exp 3 val 0: 78.00±4.00% 
Avg. ± Std. for exp 3 val 1: 81.00±6.24% 
Avg. ± Std. for exp 3 val 2: 94.00±4.64% 
Avg. ± Std. for exp 3 val 3: 91.50±3.39% 


In [90]:
from avalanche.evaluation.metrics import (
    accuracy_metrics,
    class_accuracy_metrics,
    timing_metrics,
    ram_usage_metrics,
    MAC_metrics,
)

from avalanche.training.plugins import EvaluationPlugin

from avalanche.logging import InteractiveLogger, TextLogger, CSVLogger


class ModifyEpochsP(SupervisedPlugin):

    def __init__(self):
        super().__init__()

    def after_training_exp(self, strategy, **kwargs):
        """
        Train epochs fixed as 100.
        """
        strategy.train_epochs = 50

        
# log to text file
text_logger = TextLogger(open("log.txt", "a"))

# print to stdout
interactive_logger = InteractiveLogger()

csv_logger = CSVLogger()
        
eval_plugin = EvaluationPlugin(
    accuracy_metrics(
        minibatch=True,
        epoch=True,
        epoch_running=True,
        experience=True,
        stream=True,
    ),
    class_accuracy_metrics(epoch_running=True, experience=True, classes=[0,1]),
    timing_metrics(
        epoch=True,
        experience=True,
        stream=True
    ),
    ram_usage_metrics(
        epoch=True, experience=True, stream=True
    ),
    loggers=[interactive_logger, text_logger, csv_logger],
    collect_all=True,
)



full_results = []

for manualSeed in range(5):
    
    print('Rand Seed: {}'.format(manualSeed))
    
    os.environ['PYTHONHASHSEED'] = str(manualSeed)
    torch.manual_seed(manualSeed)
    random.seed(manualSeed)
    np.random.seed(manualSeed)
    torch.backends.cudnn.deterministic = True
    
    model = edgeEEGNetBaseline(**config['indiv']['net']['params'])

    loss_fn = torch.nn.modules.loss.CrossEntropyLoss(**config['indiv']['loss_function']['params'])

    optimizer = optim.Adam(model.parameters(), lr=1e-3, eps=1e-7)

    cl_strategy = Naive(
        model, optimizer, loss_fn, train_mb_size=10, eval_mb_size=10,
        train_epochs=40, plugins=[ModifyEpochsP()], evaluator=eval_plugin
    )

    # TRAINING LOOP
    print('Starting experiment...')
    results = []
    for experience in scenario.train_stream:
        print("Start of experience: ", experience.current_experience)
        print("Current Classes: ", experience.classes_in_this_experience)

        cl_strategy.train(experience)
        print('Training completed')

        print('Computing accuracy on the whole test set')
        results.append(cl_strategy.eval(scenario.test_stream))
        
        all_metrics = cl_strategy.evaluator.get_all_metrics()
        print(f"Stored metrics: {list(all_metrics.keys())}")

        
    full_results.append(results)

Rand Seed: 0
activation relu?:  relu
Starting experiment...
Start of experience:  0
Current Classes:  [0, 1]
-- >> Start of training phase << --
100%|██████████████████████████████████████████████████████████████████████████████████| 10/10 [00:02<00:00,  4.82it/s]
Epoch 0 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 176.9375
	Time_Epoch/train_phase/train_stream/Task000 = 2.0699
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.5900
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.6000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.5900
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.4600
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.7200
100%|██████████████████████████████████████████████████████████████████████████████████| 10/10 [00:02<00:00,  4.46it/s]
Epoch 1 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 176.9375
	Time_Epoch/train_phase/train_stream/Task000 = 2.2367
	Top1_Acc_Epoch/train_phase/t

100%|██████████████████████████████████████████████████████████████████████████████████| 10/10 [00:02<00:00,  3.42it/s]
Epoch 29 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 176.9375
	Time_Epoch/train_phase/train_stream/Task000 = 2.9253
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9600
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.9600
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.9400
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.9800
100%|██████████████████████████████████████████████████████████████████████████████████| 10/10 [00:02<00:00,  3.56it/s]
Epoch 30 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 176.9375
	Time_Epoch/train_phase/train_stream/Task000 = 2.8051
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9700
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0

100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:00<00:00,  6.12it/s]
Epoch 10 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 178.0625
	Time_Epoch/train_phase/train_stream/Task000 = 0.9809
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9500
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.9000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.9500
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.9333
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.9667
100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  5.91it/s]
Epoch 11 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 182.1055
	Time_Epoch/train_phase/train_stream/Task000 = 1.0133
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9833
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0

100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:00<00:00,  6.04it/s]
Epoch 25 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 168.4688
	Time_Epoch/train_phase/train_stream/Task000 = 0.9921
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9833
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.9833
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 1.0000
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.9667
100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  5.87it/s]
Epoch 26 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 168.4688
	Time_Epoch/train_phase/train_stream/Task000 = 1.0205
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 1.0000
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 1

100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:00<00:00,  6.17it/s]
Epoch 40 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 0
	Time_Epoch/train_phase/train_stream/Task000 = 0.9691
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 1.0000
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 1.0000
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 1.0000
100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  5.72it/s]
Epoch 41 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 178.0703
	Time_Epoch/train_phase/train_stream/Task000 = 1.0474
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 1.0000
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 1.0000
	

...

100%|████████████████████████████████████████████████████████████████████████████████████| 4/4 [00:00<00:00, 46.02it/s]
> Eval on experience 1 (Task 0) from test stream ended.
	MaxRAMUsage_Experience/eval_phase/test_stream/Task000/Exp001 = 0
	Time_Exp/eval_phase/test_stream/Task000/Exp001 = 0.0872
	Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001 = 0.8250
	Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp001/0 = 0.7500
	Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp001/1 = 0.9000
-- Starting eval on experience 2 (Task 0) from test stream --
100%|████████████████████████████████████████████████████████████████████████████████████| 4/4 [00:00<00:00, 39.22it/s]
> Eval on experience 2 (Task 0) from test stream ended.
	MaxRAMUsage_Experience/eval_phase/test_stream/Task000/Exp002 = 0
	Time_Exp/eval_phase/test_stream/Task000/Exp002 = 0.1017
	Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp002 = 0.9250
	Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp002/0 = 0.8500
	Top1_ClassAcc

100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:00<00:00,  6.07it/s]
Epoch 8 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 103.6797
	Time_Epoch/train_phase/train_stream/Task000 = 0.9860
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9667
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.9667
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 1.0000
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.9333
100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  4.81it/s]
Epoch 9 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 97.7070
	Time_Epoch/train_phase/train_stream/Task000 = 1.2434
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9833
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.98

100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  5.35it/s]
Epoch 23 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 101.3594
	Time_Epoch/train_phase/train_stream/Task000 = 1.1186
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9667
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.9667
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.9667
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.9667
100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  5.26it/s]
Epoch 24 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 101.5156
	Time_Epoch/train_phase/train_stream/Task000 = 1.1390
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9833
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0

100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  4.85it/s]
Epoch 38 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 101.5156
	Time_Epoch/train_phase/train_stream/Task000 = 1.2353
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9667
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.9667
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 1.0000
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.9333
100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  5.76it/s]
Epoch 39 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 101.5156
	Time_Epoch/train_phase/train_stream/Task000 = 1.0407
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 1.0000
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 1

100%|████████████████████████████████████████████████████████████████████████████████████| 4/4 [00:00<00:00, 50.14it/s]
> Eval on experience 2 (Task 0) from test stream ended.
	MaxRAMUsage_Experience/eval_phase/test_stream/Task000/Exp002 = 0
	Time_Exp/eval_phase/test_stream/Task000/Exp002 = 0.0814
	Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp002 = 0.9500
	Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp002/0 = 0.9000
	Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp002/1 = 1.0000
-- Starting eval on experience 3 (Task 0) from test stream --
100%|████████████████████████████████████████████████████████████████████████████████████| 4/4 [00:00<00:00, 46.62it/s]
> Eval on experience 3 (Task 0) from test stream ended.
	MaxRAMUsage_Experience/eval_phase/test_stream/Task000/Exp003 = 0
	Time_Exp/eval_phase/test_stream/Task000/Exp003 = 0.0857
	Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp003 = 0.9250
	Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp003/0 = 1.0000
	Top1_ClassAcc

In [25]:
#Precision, Recall, Specificity
exp_val = np.zeros((4,4,5))

exp_tp = np.zeros((4,4,5))
exp_fp = np.zeros((4,4,5))
exp_tn = np.zeros((4,4,5))
exp_fn = np.zeros((4,4,5))
exp_precision = np.zeros((4,4,5))
exp_recall_sensitivity = np.zeros((4,4,5))
exp_specificity = np.zeros((4,4,5))

for item_no in range(len(full_results)):
    
    for no_sess in range(4):
        exp_tn[no_sess,0,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp000/0'])*20
        exp_tn[no_sess,1,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp001/0'])*20
        exp_tn[no_sess,2,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp002/0'])*20
        exp_tn[no_sess,3,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp003/0'])*20
    
        exp_tp[no_sess,0,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp000/1'])*20
        exp_tp[no_sess,1,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp001/1'])*20
        exp_tp[no_sess,2,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp002/1'])*20
        exp_tp[no_sess,3,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp003/1'])*20
        
        for j in range(4):
            exp_fp[no_sess,j,item_no] = 20 - exp_tn[no_sess,j,item_no]
            exp_fn[no_sess,j,item_no] = 20 - exp_tp[no_sess,j,item_no]
        
        for j in range(4):
            exp_precision[no_sess,j,item_no] = exp_tp[no_sess,j,item_no] / (exp_tp[no_sess,j,item_no] + exp_fp[no_sess,j,item_no])
            exp_recall_sensitivity[no_sess,j,item_no] = exp_tp[no_sess,j,item_no] / (exp_tp[no_sess,j,item_no] + exp_fn[no_sess,j,item_no])
            exp_specificity[no_sess,j,item_no] = exp_tn[no_sess,j,item_no] / (exp_tn[no_sess,j,item_no] + exp_fp[no_sess,j,item_no])
        
for i in range(4):
    for j in range(4):
        print("Precision: Avg. ± Std. for exp {} val {}: {:.2f}±{:.2f}% ".format(i, j, np.array(exp_precision[i,j]).mean()*100, np.array(exp_precision[i,j]).std()*100))
        #print("Std. for exp {} val {}: {}".format(i, j, np.array(exp_val[i,j]).std()))
    print("\n")
    
print("\n////////////////////\n")
    
for i in range(4):
    for j in range(4):
        print("Recall: Avg. ± Std. for exp {} val {}: {:.2f}±{:.2f}% ".format(i, j, np.array(exp_recall_sensitivity[i,j]).mean()*100, np.array(exp_recall_sensitivity[i,j]).std()*100))
        #print("Std. for exp {} val {}: {}".format(i, j, np.array(exp_val[i,j]).std()))
    print("\n")
        
print("\n////////////////////\n")

for i in range(4):
    for j in range(4):
        print("Specificity: Avg. ± Std. for exp {} val {}: {:.2f}±{:.2f}% ".format(i, j, np.array(exp_specificity[i,j]).mean()*100, np.array(exp_specificity[i,j]).std()*100))
        #print("Std. for exp {} val {}: {}".format(i, j, np.array(exp_val[i,j]).std()))
    print("\n")
        
print("\n////////////////////\n")

Precision: Avg. ± Std. for exp 0 val 0: 100.00±0.00% 
Precision: Avg. ± Std. for exp 0 val 1: 79.07±6.87% 
Precision: Avg. ± Std. for exp 0 val 2: 68.40±3.75% 
Precision: Avg. ± Std. for exp 0 val 3: 63.40±3.86% 


Precision: Avg. ± Std. for exp 1 val 0: 85.65±11.65% 
Precision: Avg. ± Std. for exp 1 val 1: 81.52±7.24% 
Precision: Avg. ± Std. for exp 1 val 2: 79.46±12.11% 
Precision: Avg. ± Std. for exp 1 val 3: 86.39±12.41% 


Precision: Avg. ± Std. for exp 2 val 0: 65.12±3.50% 
Precision: Avg. ± Std. for exp 2 val 1: 78.29±2.76% 
Precision: Avg. ± Std. for exp 2 val 2: 82.72±2.59% 
Precision: Avg. ± Std. for exp 2 val 3: 81.06±5.18% 


Precision: Avg. ± Std. for exp 3 val 0: 69.87±3.77% 
Precision: Avg. ± Std. for exp 3 val 1: 85.12±4.05% 
Precision: Avg. ± Std. for exp 3 val 2: 90.80±7.71% 
Precision: Avg. ± Std. for exp 3 val 3: 93.97±4.62% 



////////////////////

Recall: Avg. ± Std. for exp 0 val 0: 100.00±0.00% 
Recall: Avg. ± Std. for exp 0 val 1: 56.00±9.70% 
Recall: Avg. ± S

## ER (buf=20)

In [88]:
from avalanche.evaluation.metrics import (
    accuracy_metrics,
    class_accuracy_metrics,
    timing_metrics,
    ram_usage_metrics,
    MAC_metrics,
)

from avalanche.training.plugins import EvaluationPlugin

from avalanche.logging import InteractiveLogger, TextLogger, CSVLogger


class ModifyEpochsP(SupervisedPlugin):

    def __init__(self):
        super().__init__()

    def after_training_exp(self, strategy, **kwargs):
        """
        Train epochs fixed as 100.
        """
        strategy.train_epochs = 50

        
# log to text file
text_logger = TextLogger(open("log.txt", "a"))

# print to stdout
interactive_logger = InteractiveLogger()

csv_logger = CSVLogger()
        
eval_plugin = EvaluationPlugin(
    accuracy_metrics(
        minibatch=True,
        epoch=True,
        epoch_running=True,
        experience=True,
        stream=True,
    ),
    class_accuracy_metrics(epoch_running=True, experience=True, classes=[0,1]),
    timing_metrics(
        epoch=True,
        experience=True,
        stream=True
    ),
    ram_usage_metrics(
        epoch=True, experience=True, stream=True
    ),
    loggers=[interactive_logger, text_logger, csv_logger],
    collect_all=True,
)


full_results = []

for manualSeed in range(5):
    
    print('Rand Seed: {}'.format(manualSeed))
    
    os.environ['PYTHONHASHSEED'] = str(manualSeed)
    torch.manual_seed(manualSeed)
    random.seed(manualSeed)
    np.random.seed(manualSeed)
    torch.backends.cudnn.deterministic = True
    
    model = edgeEEGNetBaseline(**config['indiv']['net']['params'])

    loss_fn = torch.nn.modules.loss.CrossEntropyLoss(**config['indiv']['loss_function']['params'])

    optimizer = optim.Adam(model.parameters(), lr=1e-3, eps=1e-7)

    cl_strategy = Replay(
        model, optimizer, loss_fn, mem_size=20, train_mb_size=10, eval_mb_size=10,
        train_epochs=40, plugins=[ModifyEpochsP()], evaluator=eval_plugin
    )

    # TRAINING LOOP
    print('Starting experiment...')
    results = []
    for experience in scenario.train_stream:
        print("Start of experience: ", experience.current_experience)
        print("Current Classes: ", experience.classes_in_this_experience)

        cl_strategy.train(experience)
        print('Training completed')

        print('Computing accuracy on the whole test set')
        results.append(cl_strategy.eval(scenario.test_stream))
        
    full_results.append(results)

Rand Seed: 0
activation relu?:  relu
Starting experiment...
Start of experience:  0
Current Classes:  [0, 1]
-- >> Start of training phase << --
100%|██████████████████████████████████████████████████████████████████████████████████| 10/10 [00:01<00:00,  6.50it/s]
Epoch 0 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 177.0664
	Time_Epoch/train_phase/train_stream/Task000 = 1.5367
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.5900
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.6000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.5900
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.4600
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.7200
100%|██████████████████████████████████████████████████████████████████████████████████| 10/10 [00:01<00:00,  6.16it/s]
Epoch 1 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 177.0664
	Time_Epoch/train_phase/train_stream/Task000 = 1.6228
	Top1_Acc_Epoch/train_phase/t

100%|██████████████████████████████████████████████████████████████████████████████████| 10/10 [00:01<00:00,  6.13it/s]
Epoch 29 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 177.0664
	Time_Epoch/train_phase/train_stream/Task000 = 1.6294
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9600
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.9600
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.9400
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.9800
100%|██████████████████████████████████████████████████████████████████████████████████| 10/10 [00:01<00:00,  6.14it/s]
Epoch 30 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 176.9102
	Time_Epoch/train_phase/train_stream/Task000 = 1.6297
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9700
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0

100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  3.30it/s]
Epoch 13 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 189.4336
	Time_Epoch/train_phase/train_stream/Task000 = 1.8177
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9917
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.9917
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.9804
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 1.0000
100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  3.34it/s]
Epoch 14 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 189.4336
	Time_Epoch/train_phase/train_stream/Task000 = 1.7942
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9917
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.9500
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0

100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  3.29it/s]
Epoch 28 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 189.4336
	Time_Epoch/train_phase/train_stream/Task000 = 1.8202
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9917
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.9917
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 1.0000
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.9855
100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  3.31it/s]
Epoch 29 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 189.4336
	Time_Epoch/train_phase/train_stream/Task000 = 1.8109
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 1.0000
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 1

100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  3.34it/s]
Epoch 43 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 189.4336
	Time_Epoch/train_phase/train_stream/Task000 = 1.7955
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 1.0000
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 1.0000
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 1.0000
100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  3.35it/s]
Epoch 44 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 189.4336
	Time_Epoch/train_phase/train_stream/Task000 = 1.7909
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 1.0000
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 1

...

100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  3.22it/s]
Epoch 45 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 189.6094
	Time_Epoch/train_phase/train_stream/Task000 = 1.8679
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 1.0000
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 1.0000
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 1.0000
100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  3.35it/s]
Epoch 46 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 189.6094
	Time_Epoch/train_phase/train_stream/Task000 = 1.7879
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9833
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0

100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:02<00:00,  2.62it/s]
Epoch 5 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 189.6094
	Time_Epoch/train_phase/train_stream/Task000 = 2.2848
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9667
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.9500
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.9667
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.9474
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.9841
100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:02<00:00,  2.82it/s]
Epoch 6 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 193.9414
	Time_Epoch/train_phase/train_stream/Task000 = 2.1230
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9750
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.9500
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.9

100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:03<00:00,  1.83it/s]
Epoch 20 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 189.6094
	Time_Epoch/train_phase/train_stream/Task000 = 3.2674
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9917
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.9917
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 1.0000
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.9841
100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:02<00:00,  2.34it/s]
Epoch 21 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 189.6094
	Time_Epoch/train_phase/train_stream/Task000 = 2.5639
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9750
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.9500
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0

100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:02<00:00,  2.18it/s]
Epoch 35 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 197.1289
	Time_Epoch/train_phase/train_stream/Task000 = 2.7571
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9917
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.9500
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.9917
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.9825
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 1.0000
100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:02<00:00,  2.17it/s]
Epoch 36 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 189.6094
	Time_Epoch/train_phase/train_stream/Task000 = 2.7643
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9917
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0

-- >> End of training phase << --
Training completed
Computing accuracy on the whole test set
-- >> Start of eval phase << --
-- Starting eval on experience 0 (Task 0) from test stream --
100%|████████████████████████████████████████████████████████████████████████████████████| 4/4 [00:00<00:00, 31.00it/s]
> Eval on experience 0 (Task 0) from test stream ended.
	MaxRAMUsage_Experience/eval_phase/test_stream/Task000/Exp000 = 0
	Time_Exp/eval_phase/test_stream/Task000/Exp000 = 0.1245
	Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000 = 0.7750
	Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp000/0 = 0.5500
	Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp000/1 = 1.0000
-- Starting eval on experience 1 (Task 0) from test stream --
100%|████████████████████████████████████████████████████████████████████████████████████| 4/4 [00:00<00:00, 31.54it/s]
> Eval on experience 1 (Task 0) from test stream ended.
	MaxRAMUsage_Experience/eval_phase/test_stream/Task000/Exp001 = 0
	Time_Exp/ev

In [37]:
#Accuracy
exp_val = np.zeros((4,4,5))

for item_no in range(len(full_results)):

    exp_val[0,0,item_no] = (full_results[item_no][0]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000'])
    exp_val[0,1,item_no] = (full_results[item_no][0]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001'])
    exp_val[0,2,item_no] = (full_results[item_no][0]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp002'])
    exp_val[0,3,item_no] = (full_results[item_no][0]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp003'])
    exp_val[1,0,item_no] = (full_results[item_no][1]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000'])
    exp_val[1,1,item_no] = (full_results[item_no][1]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001'])
    exp_val[1,2,item_no] = (full_results[item_no][1]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp002'])
    exp_val[1,3,item_no] = (full_results[item_no][1]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp003'])
    exp_val[2,0,item_no] = (full_results[item_no][2]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000'])
    exp_val[2,1,item_no] = (full_results[item_no][2]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001'])
    exp_val[2,2,item_no] = (full_results[item_no][2]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp002'])
    exp_val[2,3,item_no] = (full_results[item_no][2]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp003'])
    exp_val[3,0,item_no] = (full_results[item_no][3]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000'])
    exp_val[3,1,item_no] = (full_results[item_no][3]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001'])
    exp_val[3,2,item_no] = (full_results[item_no][3]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp002'])
    exp_val[3,3,item_no] = (full_results[item_no][3]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp003'])
    
for i in range(4):
    for j in range(4):
        print("Avg. ± Std. for exp {} val {}: {:.2f}±{:.2f}% ".format(i, j, np.array(exp_val[i,j]).mean()*100, np.array(exp_val[i,j]).std()*100))
        #print("Std. for exp {} val {}: {}".format(i, j, np.array(exp_val[i,j]).std()))

Avg. ± Std. for exp 0 val 0: 100.00±0.00% 
Avg. ± Std. for exp 0 val 1: 70.00±2.74% 
Avg. ± Std. for exp 0 val 2: 69.00±3.74% 
Avg. ± Std. for exp 0 val 3: 64.50±4.00% 
Avg. ± Std. for exp 1 val 0: 96.50±2.00% 
Avg. ± Std. for exp 1 val 1: 84.50±4.00% 
Avg. ± Std. for exp 1 val 2: 89.00±4.90% 
Avg. ± Std. for exp 1 val 3: 84.00±5.39% 
Avg. ± Std. for exp 2 val 0: 88.00±9.41% 
Avg. ± Std. for exp 2 val 1: 85.50±1.87% 
Avg. ± Std. for exp 2 val 2: 88.00±6.20% 
Avg. ± Std. for exp 2 val 3: 86.00±3.39% 
Avg. ± Std. for exp 3 val 0: 84.50±4.30% 
Avg. ± Std. for exp 3 val 1: 87.00±4.30% 
Avg. ± Std. for exp 3 val 2: 90.00±6.71% 
Avg. ± Std. for exp 3 val 3: 91.50±2.00% 


In [27]:
#Precision, Recall, Specificity
exp_val = np.zeros((4,4,5))

exp_tp = np.zeros((4,4,5))
exp_fp = np.zeros((4,4,5))
exp_tn = np.zeros((4,4,5))
exp_fn = np.zeros((4,4,5))
exp_precision = np.zeros((4,4,5))
exp_recall_sensitivity = np.zeros((4,4,5))
exp_specificity = np.zeros((4,4,5))

for item_no in range(len(full_results)):
    
    for no_sess in range(4):
        exp_tn[no_sess,0,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp000/0'])*20
        exp_tn[no_sess,1,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp001/0'])*20
        exp_tn[no_sess,2,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp002/0'])*20
        exp_tn[no_sess,3,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp003/0'])*20
    
        exp_tp[no_sess,0,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp000/1'])*20
        exp_tp[no_sess,1,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp001/1'])*20
        exp_tp[no_sess,2,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp002/1'])*20
        exp_tp[no_sess,3,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp003/1'])*20
        
        for j in range(4):
            exp_fp[no_sess,j,item_no] = 20 - exp_tn[no_sess,j,item_no]
            exp_fn[no_sess,j,item_no] = 20 - exp_tp[no_sess,j,item_no]
        
        for j in range(4):
            exp_precision[no_sess,j,item_no] = exp_tp[no_sess,j,item_no] / (exp_tp[no_sess,j,item_no] + exp_fp[no_sess,j,item_no])
            exp_recall_sensitivity[no_sess,j,item_no] = exp_tp[no_sess,j,item_no] / (exp_tp[no_sess,j,item_no] + exp_fn[no_sess,j,item_no])
            exp_specificity[no_sess,j,item_no] = exp_tn[no_sess,j,item_no] / (exp_tn[no_sess,j,item_no] + exp_fp[no_sess,j,item_no])
        
for i in range(4):
    for j in range(4):
        print("Precision: Avg. ± Std. for exp {} val {}: {:.2f}±{:.2f}% ".format(i, j, np.array(exp_precision[i,j]).mean()*100, np.array(exp_precision[i,j]).std()*100))
        #print("Std. for exp {} val {}: {}".format(i, j, np.array(exp_val[i,j]).std()))
    print("\n")
    
print("\n////////////////////\n")
    
for i in range(4):
    for j in range(4):
        print("Recall: Avg. ± Std. for exp {} val {}: {:.2f}±{:.2f}% ".format(i, j, np.array(exp_recall_sensitivity[i,j]).mean()*100, np.array(exp_recall_sensitivity[i,j]).std()*100))
        #print("Std. for exp {} val {}: {}".format(i, j, np.array(exp_val[i,j]).std()))
    print("\n")
        
print("\n////////////////////\n")

for i in range(4):
    for j in range(4):
        print("Specificity: Avg. ± Std. for exp {} val {}: {:.2f}±{:.2f}% ".format(i, j, np.array(exp_specificity[i,j]).mean()*100, np.array(exp_specificity[i,j]).std()*100))
        #print("Std. for exp {} val {}: {}".format(i, j, np.array(exp_val[i,j]).std()))
    print("\n")
        
print("\n////////////////////\n")

Precision: Avg. ± Std. for exp 0 val 0: 100.00±0.00% 
Precision: Avg. ± Std. for exp 0 val 1: 79.07±6.87% 
Precision: Avg. ± Std. for exp 0 val 2: 68.40±3.75% 
Precision: Avg. ± Std. for exp 0 val 3: 63.40±3.86% 


Precision: Avg. ± Std. for exp 1 val 0: 95.23±2.88% 
Precision: Avg. ± Std. for exp 1 val 1: 85.08±4.95% 
Precision: Avg. ± Std. for exp 1 val 2: 84.09±8.86% 
Precision: Avg. ± Std. for exp 1 val 3: 89.25±9.32% 


Precision: Avg. ± Std. for exp 2 val 0: 84.33±11.61% 
Precision: Avg. ± Std. for exp 2 val 1: 81.22±3.73% 
Precision: Avg. ± Std. for exp 2 val 2: 81.42±7.74% 
Precision: Avg. ± Std. for exp 2 val 3: 90.57±6.09% 


Precision: Avg. ± Std. for exp 3 val 0: 81.77±8.98% 
Precision: Avg. ± Std. for exp 3 val 1: 85.57±2.62% 
Precision: Avg. ± Std. for exp 3 val 2: 84.38±9.40% 
Precision: Avg. ± Std. for exp 3 val 3: 95.84±3.79% 



////////////////////

Recall: Avg. ± Std. for exp 0 val 0: 100.00±0.00% 
Recall: Avg. ± Std. for exp 0 val 1: 56.00±9.70% 
Recall: Avg. ± Std

## ER (buf=200)

In [86]:
from avalanche.evaluation.metrics import (
    accuracy_metrics,
    class_accuracy_metrics,
    MAC_metrics,
    timing_metrics,
    ram_usage_metrics,
)

from avalanche.training.plugins import EvaluationPlugin

from avalanche.logging import InteractiveLogger, TextLogger, CSVLogger

class ModifyEpochsP(SupervisedPlugin):

    def __init__(self):
        super().__init__()

    def after_training_exp(self, strategy, **kwargs):
        """
        Train epochs fixed as 100.
        """
        strategy.train_epochs = 50

        
# log to text file
text_logger = TextLogger(open("log.txt", "a"))

# print to stdout
interactive_logger = InteractiveLogger()

csv_logger = CSVLogger()
        
eval_plugin = EvaluationPlugin(
    accuracy_metrics(
        minibatch=True,
        epoch=True,
        epoch_running=True,
        experience=True,
        stream=True,
    ),
    class_accuracy_metrics(epoch_running=True, experience=True, classes=[0,1]),
    timing_metrics(
        epoch=True,
        experience=True,
        stream=True
    ),
    ram_usage_metrics(
        epoch=True, experience=True, stream=True
    ),
    loggers=[interactive_logger, text_logger, csv_logger],
    collect_all=True,
)

full_results = []

for manualSeed in range(5):
    
    print('Rand Seed: {}'.format(manualSeed))
    
    os.environ['PYTHONHASHSEED'] = str(manualSeed)
    torch.manual_seed(manualSeed)
    random.seed(manualSeed)
    np.random.seed(manualSeed)
    torch.backends.cudnn.deterministic = True
    
    model = edgeEEGNetBaseline(**config['indiv']['net']['params'])

    loss_fn = torch.nn.modules.loss.CrossEntropyLoss(**config['indiv']['loss_function']['params'])

    optimizer = optim.Adam(model.parameters(), lr=1e-3, eps=1e-7)

    cl_strategy = Replay(
        model, optimizer, loss_fn, mem_size=200, train_mb_size=10, eval_mb_size=10,
        train_epochs=40, plugins=[ModifyEpochsP()], evaluator=eval_plugin
    )

    # TRAINING LOOP
    print('Starting experiment...')
    results = []
    for experience in scenario.train_stream:
        print("Start of experience: ", experience.current_experience)
        print("Current Classes: ", experience.classes_in_this_experience)

        cl_strategy.train(experience)
        print('Training completed')

        print('Computing accuracy on the whole test set')
        results.append(cl_strategy.eval(scenario.test_stream))
        
    full_results.append(results)

Rand Seed: 0
activation relu?:  relu
Starting experiment...
Start of experience:  0
Current Classes:  [0, 1]
-- >> Start of training phase << --
100%|██████████████████████████████████████████████████████████████████████████████████| 10/10 [00:01<00:00,  6.97it/s]
Epoch 0 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 177.4766
	Time_Epoch/train_phase/train_stream/Task000 = 1.4322
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.5900
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.6000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.5900
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.4600
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.7200
100%|██████████████████████████████████████████████████████████████████████████████████| 10/10 [00:01<00:00,  6.13it/s]
Epoch 1 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 177.4766
	Time_Epoch/train_phase/train_stream/Task000 = 1.6304
	Top1_Acc_Epoch/train_phase/t

100%|██████████████████████████████████████████████████████████████████████████████████| 10/10 [00:01<00:00,  6.08it/s]
Epoch 29 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 175.9492
	Time_Epoch/train_phase/train_stream/Task000 = 1.6438
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9600
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.9600
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.9400
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.9800
100%|██████████████████████████████████████████████████████████████████████████████████| 10/10 [00:01<00:00,  6.06it/s]
Epoch 30 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 179.6484
	Time_Epoch/train_phase/train_stream/Task000 = 1.6475
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9700
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0

100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  3.32it/s]
Epoch 13 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 189.0430
	Time_Epoch/train_phase/train_stream/Task000 = 1.8064
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9917
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.9917
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.9831
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 1.0000
100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  3.28it/s]
Epoch 14 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 189.0430
	Time_Epoch/train_phase/train_stream/Task000 = 1.8295
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9833
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0

100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  3.24it/s]
Epoch 28 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 189.0508
	Time_Epoch/train_phase/train_stream/Task000 = 1.8484
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9833
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.9833
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.9831
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.9836
100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  3.32it/s]
Epoch 29 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 189.0547
	Time_Epoch/train_phase/train_stream/Task000 = 1.8067
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9833
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.9000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0

100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  3.34it/s]
Epoch 43 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 190.4258
	Time_Epoch/train_phase/train_stream/Task000 = 1.7950
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 1.0000
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 1.0000
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 1.0000
100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  3.32it/s]
Epoch 44 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 189.0547
	Time_Epoch/train_phase/train_stream/Task000 = 1.8061
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 1.0000
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 1

...

100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  3.29it/s]
Epoch 45 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 189.5938
	Time_Epoch/train_phase/train_stream/Task000 = 1.8196
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9833
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.9833
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.9828
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.9839
100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  3.35it/s]
Epoch 46 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 189.5938
	Time_Epoch/train_phase/train_stream/Task000 = 1.7865
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 1.0000
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 1

100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  3.36it/s]
Epoch 5 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 192.2461
	Time_Epoch/train_phase/train_stream/Task000 = 1.7842
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9750
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.9750
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.9683
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.9825
100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  3.30it/s]
Epoch 6 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 189.6055
	Time_Epoch/train_phase/train_stream/Task000 = 1.8179
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9500
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.9

100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  3.32it/s]
Epoch 20 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 189.6055
	Time_Epoch/train_phase/train_stream/Task000 = 1.8097
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9583
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.9500
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.9583
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.9483
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.9677
100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  3.36it/s]
Epoch 21 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 189.6055
	Time_Epoch/train_phase/train_stream/Task000 = 1.7856
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9833
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0

100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  3.31it/s]
Epoch 35 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 187.8242
	Time_Epoch/train_phase/train_stream/Task000 = 1.8126
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9833
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.9833
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.9667
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 1.0000
100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  3.35it/s]
Epoch 36 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 189.6055
	Time_Epoch/train_phase/train_stream/Task000 = 1.7919
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9667
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.9500
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0

-- >> End of training phase << --
Training completed
Computing accuracy on the whole test set
-- >> Start of eval phase << --
-- Starting eval on experience 0 (Task 0) from test stream --
100%|████████████████████████████████████████████████████████████████████████████████████| 4/4 [00:00<00:00, 54.61it/s]
> Eval on experience 0 (Task 0) from test stream ended.
	MaxRAMUsage_Experience/eval_phase/test_stream/Task000/Exp000 = 0
	Time_Exp/eval_phase/test_stream/Task000/Exp000 = 0.0723
	Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000 = 1.0000
	Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp000/0 = 1.0000
	Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp000/1 = 1.0000
-- Starting eval on experience 1 (Task 0) from test stream --
100%|████████████████████████████████████████████████████████████████████████████████████| 4/4 [00:00<00:00, 52.63it/s]
> Eval on experience 1 (Task 0) from test stream ended.
	MaxRAMUsage_Experience/eval_phase/test_stream/Task000/Exp001 = 0
	Time_Exp/ev

In [40]:
#Accuracy
exp_val = np.zeros((4,4,5))

for item_no in range(len(full_results)):

    exp_val[0,0,item_no] = (full_results[item_no][0]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000'])
    exp_val[0,1,item_no] = (full_results[item_no][0]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001'])
    exp_val[0,2,item_no] = (full_results[item_no][0]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp002'])
    exp_val[0,3,item_no] = (full_results[item_no][0]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp003'])
    exp_val[1,0,item_no] = (full_results[item_no][1]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000'])
    exp_val[1,1,item_no] = (full_results[item_no][1]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001'])
    exp_val[1,2,item_no] = (full_results[item_no][1]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp002'])
    exp_val[1,3,item_no] = (full_results[item_no][1]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp003'])
    exp_val[2,0,item_no] = (full_results[item_no][2]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000'])
    exp_val[2,1,item_no] = (full_results[item_no][2]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001'])
    exp_val[2,2,item_no] = (full_results[item_no][2]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp002'])
    exp_val[2,3,item_no] = (full_results[item_no][2]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp003'])
    exp_val[3,0,item_no] = (full_results[item_no][3]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000'])
    exp_val[3,1,item_no] = (full_results[item_no][3]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001'])
    exp_val[3,2,item_no] = (full_results[item_no][3]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp002'])
    exp_val[3,3,item_no] = (full_results[item_no][3]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp003'])
    
for i in range(4):
    for j in range(4):
        print("Avg. ± Std. for exp {} val {}: {:.2f}±{:.2f}% ".format(i, j, np.array(exp_val[i,j]).mean()*100, np.array(exp_val[i,j]).std()*100))
        #print("Std. for exp {} val {}: {}".format(i, j, np.array(exp_val[i,j]).std()))

Avg. ± Std. for exp 0 val 0: 100.00±0.00% 
Avg. ± Std. for exp 0 val 1: 70.00±2.74% 
Avg. ± Std. for exp 0 val 2: 69.00±3.74% 
Avg. ± Std. for exp 0 val 3: 64.50±4.00% 
Avg. ± Std. for exp 1 val 0: 100.00±0.00% 
Avg. ± Std. for exp 1 val 1: 83.00±4.00% 
Avg. ± Std. for exp 1 val 2: 88.50±5.39% 
Avg. ± Std. for exp 1 val 3: 79.50±1.87% 
Avg. ± Std. for exp 2 val 0: 99.50±1.00% 
Avg. ± Std. for exp 2 val 1: 85.00±1.58% 
Avg. ± Std. for exp 2 val 2: 92.00±2.92% 
Avg. ± Std. for exp 2 val 3: 86.50±6.44% 
Avg. ± Std. for exp 3 val 0: 97.00±2.92% 
Avg. ± Std. for exp 3 val 1: 86.50±3.39% 
Avg. ± Std. for exp 3 val 2: 92.50±11.29% 
Avg. ± Std. for exp 3 val 3: 87.50±3.54% 


In [29]:
#Precision, Recall, Specificity
exp_val = np.zeros((4,4,5))

exp_tp = np.zeros((4,4,5))
exp_fp = np.zeros((4,4,5))
exp_tn = np.zeros((4,4,5))
exp_fn = np.zeros((4,4,5))
exp_precision = np.zeros((4,4,5))
exp_recall_sensitivity = np.zeros((4,4,5))
exp_specificity = np.zeros((4,4,5))

for item_no in range(len(full_results)):
    
    for no_sess in range(4):
        exp_tn[no_sess,0,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp000/0'])*20
        exp_tn[no_sess,1,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp001/0'])*20
        exp_tn[no_sess,2,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp002/0'])*20
        exp_tn[no_sess,3,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp003/0'])*20
    
        exp_tp[no_sess,0,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp000/1'])*20
        exp_tp[no_sess,1,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp001/1'])*20
        exp_tp[no_sess,2,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp002/1'])*20
        exp_tp[no_sess,3,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp003/1'])*20
        
        for j in range(4):
            exp_fp[no_sess,j,item_no] = 20 - exp_tn[no_sess,j,item_no]
            exp_fn[no_sess,j,item_no] = 20 - exp_tp[no_sess,j,item_no]
        
        for j in range(4):
            exp_precision[no_sess,j,item_no] = exp_tp[no_sess,j,item_no] / (exp_tp[no_sess,j,item_no] + exp_fp[no_sess,j,item_no])
            exp_recall_sensitivity[no_sess,j,item_no] = exp_tp[no_sess,j,item_no] / (exp_tp[no_sess,j,item_no] + exp_fn[no_sess,j,item_no])
            exp_specificity[no_sess,j,item_no] = exp_tn[no_sess,j,item_no] / (exp_tn[no_sess,j,item_no] + exp_fp[no_sess,j,item_no])
        
for i in range(4):
    for j in range(4):
        print("Precision: Avg. ± Std. for exp {} val {}: {:.2f}±{:.2f}% ".format(i, j, np.array(exp_precision[i,j]).mean()*100, np.array(exp_precision[i,j]).std()*100))
        #print("Std. for exp {} val {}: {}".format(i, j, np.array(exp_val[i,j]).std()))
    print("\n")
    
print("\n////////////////////\n")
    
for i in range(4):
    for j in range(4):
        print("Recall: Avg. ± Std. for exp {} val {}: {:.2f}±{:.2f}% ".format(i, j, np.array(exp_recall_sensitivity[i,j]).mean()*100, np.array(exp_recall_sensitivity[i,j]).std()*100))
        #print("Std. for exp {} val {}: {}".format(i, j, np.array(exp_val[i,j]).std()))
    print("\n")
        
print("\n////////////////////\n")

for i in range(4):
    for j in range(4):
        print("Specificity: Avg. ± Std. for exp {} val {}: {:.2f}±{:.2f}% ".format(i, j, np.array(exp_specificity[i,j]).mean()*100, np.array(exp_specificity[i,j]).std()*100))
        #print("Std. for exp {} val {}: {}".format(i, j, np.array(exp_val[i,j]).std()))
    print("\n")
        
print("\n////////////////////\n")

Precision: Avg. ± Std. for exp 0 val 0: 100.00±0.00% 
Precision: Avg. ± Std. for exp 0 val 1: 79.07±6.87% 
Precision: Avg. ± Std. for exp 0 val 2: 68.40±3.75% 
Precision: Avg. ± Std. for exp 0 val 3: 63.40±3.86% 


Precision: Avg. ± Std. for exp 1 val 0: 100.00±0.00% 
Precision: Avg. ± Std. for exp 1 val 1: 82.76±7.39% 
Precision: Avg. ± Std. for exp 1 val 2: 86.48±11.19% 
Precision: Avg. ± Std. for exp 1 val 3: 85.68±9.44% 


Precision: Avg. ± Std. for exp 2 val 0: 99.05±1.90% 
Precision: Avg. ± Std. for exp 2 val 1: 82.09±5.88% 
Precision: Avg. ± Std. for exp 2 val 2: 86.42±4.27% 
Precision: Avg. ± Std. for exp 2 val 3: 95.46±6.02% 


Precision: Avg. ± Std. for exp 3 val 0: 95.44±4.77% 
Precision: Avg. ± Std. for exp 3 val 1: 86.42±4.48% 
Precision: Avg. ± Std. for exp 3 val 2: 89.64±13.70% 
Precision: Avg. ± Std. for exp 3 val 3: 91.70±6.66% 



////////////////////

Recall: Avg. ± Std. for exp 0 val 0: 100.00±0.00% 
Recall: Avg. ± Std. for exp 0 val 1: 56.00±9.70% 
Recall: Avg. ± S

## LwF

In [84]:
from avalanche.evaluation.metrics import (
    accuracy_metrics,
    class_accuracy_metrics,
    MAC_metrics,
    timing_metrics,
    ram_usage_metrics,
)

from avalanche.training.plugins import EvaluationPlugin

from avalanche.logging import InteractiveLogger, TextLogger, CSVLogger

class ModifyEpochsP(SupervisedPlugin):

    def __init__(self):
        super().__init__()

    def after_training_exp(self, strategy, **kwargs):
        """
        Train epochs fixed as 100.
        """
        strategy.train_epochs = 50

        
# log to text file
text_logger = TextLogger(open("log.txt", "a"))

# print to stdout
interactive_logger = InteractiveLogger()

csv_logger = CSVLogger()
        
eval_plugin = EvaluationPlugin(
    accuracy_metrics(
        minibatch=True,
        epoch=True,
        epoch_running=True,
        experience=True,
        stream=True,
    ),
    class_accuracy_metrics(epoch_running=True, experience=True, classes=[0,1]),
    timing_metrics(
        epoch=True,
        experience=True,
        stream=True
    ),
    ram_usage_metrics(
        epoch=True, experience=True, stream=True
    ),
    loggers=[interactive_logger, text_logger, csv_logger],
    collect_all=True,
)


full_results = []

for manualSeed in range(5):
    
    print('Rand Seed: {}'.format(manualSeed))
    
    os.environ['PYTHONHASHSEED'] = str(manualSeed)
    torch.manual_seed(manualSeed)
    random.seed(manualSeed)
    np.random.seed(manualSeed)
    torch.backends.cudnn.deterministic = True
    
    model = edgeEEGNetBaseline(**config['indiv']['net']['params'])

    loss_fn = torch.nn.modules.loss.CrossEntropyLoss(**config['indiv']['loss_function']['params'])

    optimizer = optim.Adam(model.parameters(), lr=1e-3, eps=1e-7)

    cl_strategy = LwF(
        model, optimizer, loss_fn, alpha=1, temperature=2, train_mb_size=10, eval_mb_size=10,
        train_epochs=40, plugins=[ModifyEpochsP()], evaluator=eval_plugin
    )

    # TRAINING LOOP
    print('Starting experiment...')
    results = []
    for experience in scenario.train_stream:
        print("Start of experience: ", experience.current_experience)
        print("Current Classes: ", experience.classes_in_this_experience)

        cl_strategy.train(experience)
        print('Training completed')

        print('Computing accuracy on the whole test set')
        results.append(cl_strategy.eval(scenario.test_stream))
        
    full_results.append(results)

Rand Seed: 0
activation relu?:  relu
Starting experiment...
Start of experience:  0
Current Classes:  [0, 1]
-- >> Start of training phase << --
100%|██████████████████████████████████████████████████████████████████████████████████| 10/10 [00:01<00:00,  9.14it/s]
Epoch 0 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 196.7852
	Time_Epoch/train_phase/train_stream/Task000 = 1.0927
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.5900
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.6000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.5900
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.4600
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.7200
100%|██████████████████████████████████████████████████████████████████████████████████| 10/10 [00:01<00:00,  9.21it/s]
Epoch 1 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 196.9453
	Time_Epoch/train_phase/train_stream/Task000 = 1.0841
	Top1_Acc_Epoch/train_phase/t

100%|██████████████████████████████████████████████████████████████████████████████████| 10/10 [00:01<00:00,  7.99it/s]
Epoch 29 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 196.9883
	Time_Epoch/train_phase/train_stream/Task000 = 1.2507
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9600
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.9600
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.9400
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.9800
100%|██████████████████████████████████████████████████████████████████████████████████| 10/10 [00:01<00:00,  8.09it/s]
Epoch 30 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 187.3945
	Time_Epoch/train_phase/train_stream/Task000 = 1.2343
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9700
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0

100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:00<00:00,  7.16it/s]
Epoch 13 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 0
	Time_Epoch/train_phase/train_stream/Task000 = 0.8378
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9833
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.9833
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 1.0000
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.9667
100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:00<00:00,  6.69it/s]
Epoch 14 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 197.0781
	Time_Epoch/train_phase/train_stream/Task000 = 0.8960
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9833
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.9833
	

100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:00<00:00,  6.24it/s]
Epoch 28 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 197.7578
	Time_Epoch/train_phase/train_stream/Task000 = 0.9602
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9500
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.8000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.9500
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.9667
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.9333
100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:00<00:00,  7.31it/s]
Epoch 29 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 197.7578
	Time_Epoch/train_phase/train_stream/Task000 = 0.8196
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9500
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.9000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0

100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:00<00:00,  6.56it/s]
Epoch 43 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 188.1641
	Time_Epoch/train_phase/train_stream/Task000 = 0.9150
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9500
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.9000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.9500
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.9333
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.9667
100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:00<00:00,  6.79it/s]
Epoch 44 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 197.7578
	Time_Epoch/train_phase/train_stream/Task000 = 0.8825
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 1.0000
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 1

...

100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  5.55it/s]
Epoch 45 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 176.6875
	Time_Epoch/train_phase/train_stream/Task000 = 1.0808
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9833
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.9833
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 1.0000
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.9667
100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  5.52it/s]
Epoch 46 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 177.1094
	Time_Epoch/train_phase/train_stream/Task000 = 1.0868
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9833
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0

100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  5.48it/s]
Epoch 5 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 170.6953
	Time_Epoch/train_phase/train_stream/Task000 = 1.0925
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9167
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.8000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.9167
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.8667
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.9667
100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  5.65it/s]
Epoch 6 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 177.1250
	Time_Epoch/train_phase/train_stream/Task000 = 1.0603
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.8833
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.8

100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  5.48it/s]
Epoch 20 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 177.1328
	Time_Epoch/train_phase/train_stream/Task000 = 1.0946
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 1.0000
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 1.0000
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 1.0000
100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  5.56it/s]
Epoch 21 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 176.0898
	Time_Epoch/train_phase/train_stream/Task000 = 1.0787
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9667
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0

100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  5.50it/s]
Epoch 35 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 175.6484
	Time_Epoch/train_phase/train_stream/Task000 = 1.0906
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9667
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.9667
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.9333
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 1.0000
100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  5.51it/s]
Epoch 36 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 177.1484
	Time_Epoch/train_phase/train_stream/Task000 = 1.0876
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9833
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0

-- >> End of training phase << --
Training completed
Computing accuracy on the whole test set
-- >> Start of eval phase << --
-- Starting eval on experience 0 (Task 0) from test stream --
100%|████████████████████████████████████████████████████████████████████████████████████| 4/4 [00:00<00:00, 60.43it/s]
> Eval on experience 0 (Task 0) from test stream ended.
	MaxRAMUsage_Experience/eval_phase/test_stream/Task000/Exp000 = 0
	Time_Exp/eval_phase/test_stream/Task000/Exp000 = 0.0651
	Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000 = 0.7000
	Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp000/0 = 0.4000
	Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp000/1 = 1.0000
-- Starting eval on experience 1 (Task 0) from test stream --
100%|████████████████████████████████████████████████████████████████████████████████████| 4/4 [00:00<00:00, 58.19it/s]
> Eval on experience 1 (Task 0) from test stream ended.
	MaxRAMUsage_Experience/eval_phase/test_stream/Task000/Exp001 = 0
	Time_Exp/ev

In [43]:
#Accuracy
exp_val = np.zeros((4,4,5))

for item_no in range(len(full_results)):

    exp_val[0,0,item_no] = (full_results[item_no][0]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000'])
    exp_val[0,1,item_no] = (full_results[item_no][0]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001'])
    exp_val[0,2,item_no] = (full_results[item_no][0]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp002'])
    exp_val[0,3,item_no] = (full_results[item_no][0]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp003'])
    exp_val[1,0,item_no] = (full_results[item_no][1]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000'])
    exp_val[1,1,item_no] = (full_results[item_no][1]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001'])
    exp_val[1,2,item_no] = (full_results[item_no][1]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp002'])
    exp_val[1,3,item_no] = (full_results[item_no][1]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp003'])
    exp_val[2,0,item_no] = (full_results[item_no][2]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000'])
    exp_val[2,1,item_no] = (full_results[item_no][2]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001'])
    exp_val[2,2,item_no] = (full_results[item_no][2]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp002'])
    exp_val[2,3,item_no] = (full_results[item_no][2]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp003'])
    exp_val[3,0,item_no] = (full_results[item_no][3]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000'])
    exp_val[3,1,item_no] = (full_results[item_no][3]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001'])
    exp_val[3,2,item_no] = (full_results[item_no][3]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp002'])
    exp_val[3,3,item_no] = (full_results[item_no][3]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp003'])
    
for i in range(4):
    for j in range(4):
        print("Avg. ± Std. for exp {} val {}: {:.2f}±{:.2f}% ".format(i, j, np.array(exp_val[i,j]).mean()*100, np.array(exp_val[i,j]).std()*100))
        #print("Std. for exp {} val {}: {}".format(i, j, np.array(exp_val[i,j]).std()))

Avg. ± Std. for exp 0 val 0: 100.00±0.00% 
Avg. ± Std. for exp 0 val 1: 70.00±2.74% 
Avg. ± Std. for exp 0 val 2: 69.00±3.74% 
Avg. ± Std. for exp 0 val 3: 64.50±4.00% 
Avg. ± Std. for exp 1 val 0: 98.00±1.00% 
Avg. ± Std. for exp 1 val 1: 84.50±2.92% 
Avg. ± Std. for exp 1 val 2: 84.50±3.67% 
Avg. ± Std. for exp 1 val 3: 76.50±4.36% 
Avg. ± Std. for exp 2 val 0: 81.50±8.60% 
Avg. ± Std. for exp 2 val 1: 83.50±3.00% 
Avg. ± Std. for exp 2 val 2: 86.00±6.04% 
Avg. ± Std. for exp 2 val 3: 87.50±4.74% 
Avg. ± Std. for exp 3 val 0: 80.50±6.60% 
Avg. ± Std. for exp 3 val 1: 79.00±4.90% 
Avg. ± Std. for exp 3 val 2: 98.00±1.87% 
Avg. ± Std. for exp 3 val 3: 93.00±1.87% 


In [31]:
#Precision, Recall, Specificity
exp_val = np.zeros((4,4,5))

exp_tp = np.zeros((4,4,5))
exp_fp = np.zeros((4,4,5))
exp_tn = np.zeros((4,4,5))
exp_fn = np.zeros((4,4,5))
exp_precision = np.zeros((4,4,5))
exp_recall_sensitivity = np.zeros((4,4,5))
exp_specificity = np.zeros((4,4,5))

for item_no in range(len(full_results)):
    
    for no_sess in range(4):
        exp_tn[no_sess,0,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp000/0'])*20
        exp_tn[no_sess,1,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp001/0'])*20
        exp_tn[no_sess,2,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp002/0'])*20
        exp_tn[no_sess,3,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp003/0'])*20
    
        exp_tp[no_sess,0,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp000/1'])*20
        exp_tp[no_sess,1,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp001/1'])*20
        exp_tp[no_sess,2,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp002/1'])*20
        exp_tp[no_sess,3,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp003/1'])*20
        
        for j in range(4):
            exp_fp[no_sess,j,item_no] = 20 - exp_tn[no_sess,j,item_no]
            exp_fn[no_sess,j,item_no] = 20 - exp_tp[no_sess,j,item_no]
        
        for j in range(4):
            exp_precision[no_sess,j,item_no] = exp_tp[no_sess,j,item_no] / (exp_tp[no_sess,j,item_no] + exp_fp[no_sess,j,item_no])
            exp_recall_sensitivity[no_sess,j,item_no] = exp_tp[no_sess,j,item_no] / (exp_tp[no_sess,j,item_no] + exp_fn[no_sess,j,item_no])
            exp_specificity[no_sess,j,item_no] = exp_tn[no_sess,j,item_no] / (exp_tn[no_sess,j,item_no] + exp_fp[no_sess,j,item_no])
        
for i in range(4):
    for j in range(4):
        print("Precision: Avg. ± Std. for exp {} val {}: {:.2f}±{:.2f}% ".format(i, j, np.array(exp_precision[i,j]).mean()*100, np.array(exp_precision[i,j]).std()*100))
        #print("Std. for exp {} val {}: {}".format(i, j, np.array(exp_val[i,j]).std()))
    print("\n")
    
print("\n////////////////////\n")
    
for i in range(4):
    for j in range(4):
        print("Recall: Avg. ± Std. for exp {} val {}: {:.2f}±{:.2f}% ".format(i, j, np.array(exp_recall_sensitivity[i,j]).mean()*100, np.array(exp_recall_sensitivity[i,j]).std()*100))
        #print("Std. for exp {} val {}: {}".format(i, j, np.array(exp_val[i,j]).std()))
    print("\n")
        
print("\n////////////////////\n")

for i in range(4):
    for j in range(4):
        print("Specificity: Avg. ± Std. for exp {} val {}: {:.2f}±{:.2f}% ".format(i, j, np.array(exp_specificity[i,j]).mean()*100, np.array(exp_specificity[i,j]).std()*100))
        #print("Std. for exp {} val {}: {}".format(i, j, np.array(exp_val[i,j]).std()))
    print("\n")
        
print("\n////////////////////\n")

Precision: Avg. ± Std. for exp 0 val 0: 100.00±0.00% 
Precision: Avg. ± Std. for exp 0 val 1: 79.07±6.87% 
Precision: Avg. ± Std. for exp 0 val 2: 68.40±3.75% 
Precision: Avg. ± Std. for exp 0 val 3: 63.40±3.86% 


Precision: Avg. ± Std. for exp 1 val 0: 96.19±1.90% 
Precision: Avg. ± Std. for exp 1 val 1: 92.85±4.39% 
Precision: Avg. ± Std. for exp 1 val 2: 78.96±5.23% 
Precision: Avg. ± Std. for exp 1 val 3: 78.99±4.35% 


Precision: Avg. ± Std. for exp 2 val 0: 74.12±9.00% 
Precision: Avg. ± Std. for exp 2 val 1: 81.38±6.44% 
Precision: Avg. ± Std. for exp 2 val 2: 78.78±6.92% 
Precision: Avg. ± Std. for exp 2 val 3: 85.42±8.66% 


Precision: Avg. ± Std. for exp 3 val 0: 73.72±8.21% 
Precision: Avg. ± Std. for exp 3 val 1: 85.20±3.43% 
Precision: Avg. ± Std. for exp 3 val 2: 96.28±3.43% 
Precision: Avg. ± Std. for exp 3 val 3: 97.84±2.65% 



////////////////////

Recall: Avg. ± Std. for exp 0 val 0: 100.00±0.00% 
Recall: Avg. ± Std. for exp 0 val 1: 56.00±9.70% 
Recall: Avg. ± Std.

## EWC

In [79]:
from avalanche.evaluation.metrics import (
    accuracy_metrics,
    class_accuracy_metrics,
    MAC_metrics,
    timing_metrics,
    ram_usage_metrics,
    disk_usage_metrics,
)

from avalanche.training.plugins import EvaluationPlugin

from avalanche.logging import InteractiveLogger, TextLogger, CSVLogger

class ModifyEpochsP(SupervisedPlugin):

    def __init__(self):
        super().__init__()

    def after_training_exp(self, strategy, **kwargs):
        """
        Train epochs fixed as 100.
        """
        strategy.train_epochs = 50

        
# log to text file
text_logger = TextLogger(open("log.txt", "a"))

# print to stdout
interactive_logger = InteractiveLogger()

csv_logger = CSVLogger()
        
eval_plugin = EvaluationPlugin(
    accuracy_metrics(
        minibatch=True,
        epoch=True,
        epoch_running=True,
        experience=True,
        stream=True,
    ),
    class_accuracy_metrics(epoch_running=True, experience=True, classes=[0,1]),
    timing_metrics(
        epoch=True,
        experience=True,
        stream=True
    ),
    ram_usage_metrics(
        epoch=True, experience=True, stream=True
    ),
    loggers=[interactive_logger, text_logger, csv_logger],
    collect_all=True,
)

full_results = []

for manualSeed in range(5):
    
    print('Rand Seed: {}'.format(manualSeed))
    
    os.environ['PYTHONHASHSEED'] = str(manualSeed)
    torch.manual_seed(manualSeed)
    random.seed(manualSeed)
    np.random.seed(manualSeed)
    torch.backends.cudnn.deterministic = True
    
    model = edgeEEGNetBaseline(**config['indiv']['net']['params'])

    loss_fn = torch.nn.modules.loss.CrossEntropyLoss(**config['indiv']['loss_function']['params'])

    optimizer = optim.Adam(model.parameters(), lr=1e-3, eps=1e-7)

    cl_strategy = EWC(
        model, optimizer, loss_fn, ewc_lambda=10000, train_mb_size=10, eval_mb_size=10,
        train_epochs=40, plugins=[ModifyEpochsP()], evaluator=eval_plugin
    )

    # TRAINING LOOP
    print('Starting experiment...')
    results = []
    for experience in scenario.train_stream:
        print("Start of experience: ", experience.current_experience)
        print("Current Classes: ", experience.classes_in_this_experience)

        cl_strategy.train(experience)
        print('Training completed')

        print('Computing accuracy on the whole test set')
        results.append(cl_strategy.eval(scenario.test_stream))
        
    full_results.append(results)

Rand Seed: 0
activation relu?:  relu
Starting experiment...
Start of experience:  0
Current Classes:  [0, 1]
-- >> Start of training phase << --
100%|██████████████████████████████████████████████████████████████████████████████████| 10/10 [00:01<00:00,  6.46it/s]
Epoch 0 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 283.7656
	Time_Epoch/train_phase/train_stream/Task000 = 1.5436
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.5900
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.6000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.5900
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.4600
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.7200
100%|██████████████████████████████████████████████████████████████████████████████████| 10/10 [00:01<00:00,  5.71it/s]
Epoch 1 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 283.7656
	Time_Epoch/train_phase/train_stream/Task000 = 1.7485
	Top1_Acc_Epoch/train_phase/t

100%|██████████████████████████████████████████████████████████████████████████████████| 10/10 [00:01<00:00,  6.08it/s]
Epoch 29 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 283.7812
	Time_Epoch/train_phase/train_stream/Task000 = 1.6427
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9600
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.9600
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.9400
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.9800
100%|██████████████████████████████████████████████████████████████████████████████████| 10/10 [00:01<00:00,  6.03it/s]
Epoch 30 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 283.7812
	Time_Epoch/train_phase/train_stream/Task000 = 1.6561
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9700
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0

100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  5.63it/s]
Epoch 13 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 285.3867
	Time_Epoch/train_phase/train_stream/Task000 = 1.0648
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9667
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.9000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.9667
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.9667
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.9667
100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  5.93it/s]
Epoch 14 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 285.3867
	Time_Epoch/train_phase/train_stream/Task000 = 1.0107
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 1.0000
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 1

100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  5.74it/s]
Epoch 28 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 285.2422
	Time_Epoch/train_phase/train_stream/Task000 = 1.0443
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 1.0000
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 1.0000
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 1.0000
100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  5.22it/s]
Epoch 29 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 285.3984
	Time_Epoch/train_phase/train_stream/Task000 = 1.1487
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 1.0000
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 1

100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  5.31it/s]
Epoch 43 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 285.4180
	Time_Epoch/train_phase/train_stream/Task000 = 1.1276
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9833
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.9833
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.9667
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 1.0000
100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  5.85it/s]
Epoch 44 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 285.4180
	Time_Epoch/train_phase/train_stream/Task000 = 1.0250
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9500
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.9000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0

...

100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:00<00:00,  6.11it/s]
Epoch 45 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 234.0273
	Time_Epoch/train_phase/train_stream/Task000 = 0.9795
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.8000
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.8000
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.8667
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.7333
100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:00<00:00,  6.05it/s]
Epoch 46 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 234.8516
	Time_Epoch/train_phase/train_stream/Task000 = 0.9899
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.8167
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.8000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0

100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  5.95it/s]
Epoch 5 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 234.8672
	Time_Epoch/train_phase/train_stream/Task000 = 1.0073
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.8000
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.9000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.8000
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.9000
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.7000
100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:00<00:00,  6.06it/s]
Epoch 6 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 234.8711
	Time_Epoch/train_phase/train_stream/Task000 = 0.9886
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.7667
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.8000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.7

100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  5.82it/s]
Epoch 20 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 232.5664
	Time_Epoch/train_phase/train_stream/Task000 = 1.0284
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.7667
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.8000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.7667
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.8333
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.7000
100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  5.94it/s]
Epoch 21 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 230.2148
	Time_Epoch/train_phase/train_stream/Task000 = 1.0091
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.8333
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.8000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0

100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  5.98it/s]
Epoch 35 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 234.9062
	Time_Epoch/train_phase/train_stream/Task000 = 1.0028
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.6667
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.9000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.6667
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.6667
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.6667
100%|████████████████████████████████████████████████████████████████████████████████████| 6/6 [00:01<00:00,  5.97it/s]
Epoch 36 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 234.9062
	Time_Epoch/train_phase/train_stream/Task000 = 1.0047
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.8000
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.7000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0

-- >> End of training phase << --
Training completed
Computing accuracy on the whole test set
-- >> Start of eval phase << --
-- Starting eval on experience 0 (Task 0) from test stream --
100%|████████████████████████████████████████████████████████████████████████████████████| 4/4 [00:00<00:00, 55.51it/s]
> Eval on experience 0 (Task 0) from test stream ended.
	MaxRAMUsage_Experience/eval_phase/test_stream/Task000/Exp000 = 0
	Time_Exp/eval_phase/test_stream/Task000/Exp000 = 0.0722
	Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000 = 0.9750
	Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp000/0 = 0.9500
	Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp000/1 = 1.0000
-- Starting eval on experience 1 (Task 0) from test stream --
100%|████████████████████████████████████████████████████████████████████████████████████| 4/4 [00:00<00:00, 54.86it/s]
> Eval on experience 1 (Task 0) from test stream ended.
	MaxRAMUsage_Experience/eval_phase/test_stream/Task000/Exp001 = 0
	Time_Exp/ev

In [80]:
#Accuracy
exp_val = np.zeros((4,4,5))

for item_no in range(len(full_results)):

    exp_val[0,0,item_no] = (full_results[item_no][0]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000'])
    exp_val[0,1,item_no] = (full_results[item_no][0]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001'])
    exp_val[0,2,item_no] = (full_results[item_no][0]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp002'])
    exp_val[0,3,item_no] = (full_results[item_no][0]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp003'])
    exp_val[1,0,item_no] = (full_results[item_no][1]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000'])
    exp_val[1,1,item_no] = (full_results[item_no][1]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001'])
    exp_val[1,2,item_no] = (full_results[item_no][1]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp002'])
    exp_val[1,3,item_no] = (full_results[item_no][1]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp003'])
    exp_val[2,0,item_no] = (full_results[item_no][2]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000'])
    exp_val[2,1,item_no] = (full_results[item_no][2]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001'])
    exp_val[2,2,item_no] = (full_results[item_no][2]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp002'])
    exp_val[2,3,item_no] = (full_results[item_no][2]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp003'])
    exp_val[3,0,item_no] = (full_results[item_no][3]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000'])
    exp_val[3,1,item_no] = (full_results[item_no][3]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001'])
    exp_val[3,2,item_no] = (full_results[item_no][3]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp002'])
    exp_val[3,3,item_no] = (full_results[item_no][3]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp003'])
    
for i in range(4):
    for j in range(4):
        print("Avg. ± Std. for exp {} val {}: {:.2f}±{:.2f}% ".format(i, j, np.array(exp_val[i,j]).mean()*100, np.array(exp_val[i,j]).std()*100))
        #print("Std. for exp {} val {}: {}".format(i, j, np.array(exp_val[i,j]).std()))

Avg. ± Std. for exp 0 val 0: 100.00±0.00% 
Avg. ± Std. for exp 0 val 1: 70.00±2.74% 
Avg. ± Std. for exp 0 val 2: 69.00±3.74% 
Avg. ± Std. for exp 0 val 3: 64.50±4.00% 
Avg. ± Std. for exp 1 val 0: 96.50±2.00% 
Avg. ± Std. for exp 1 val 1: 78.50±5.83% 
Avg. ± Std. for exp 1 val 2: 86.50±4.36% 
Avg. ± Std. for exp 1 val 3: 77.00±5.57% 
Avg. ± Std. for exp 2 val 0: 88.50±8.15% 
Avg. ± Std. for exp 2 val 1: 80.00±2.74% 
Avg. ± Std. for exp 2 val 2: 83.50±2.00% 
Avg. ± Std. for exp 2 val 3: 73.50±5.61% 
Avg. ± Std. for exp 3 val 0: 97.00±1.00% 
Avg. ± Std. for exp 3 val 1: 76.00±5.39% 
Avg. ± Std. for exp 3 val 2: 86.50±5.15% 
Avg. ± Std. for exp 3 val 3: 74.00±5.83% 


In [33]:
#Precision, Recall, Specificity
exp_val = np.zeros((4,4,5))

exp_tp = np.zeros((4,4,5))
exp_fp = np.zeros((4,4,5))
exp_tn = np.zeros((4,4,5))
exp_fn = np.zeros((4,4,5))
exp_precision = np.zeros((4,4,5))
exp_recall_sensitivity = np.zeros((4,4,5))
exp_specificity = np.zeros((4,4,5))

for item_no in range(len(full_results)):
    
    for no_sess in range(4):
        exp_tn[no_sess,0,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp000/0'])*20
        exp_tn[no_sess,1,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp001/0'])*20
        exp_tn[no_sess,2,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp002/0'])*20
        exp_tn[no_sess,3,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp003/0'])*20
    
        exp_tp[no_sess,0,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp000/1'])*20
        exp_tp[no_sess,1,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp001/1'])*20
        exp_tp[no_sess,2,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp002/1'])*20
        exp_tp[no_sess,3,item_no] = (full_results[item_no][no_sess]['Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp003/1'])*20
        
        for j in range(4):
            exp_fp[no_sess,j,item_no] = 20 - exp_tn[no_sess,j,item_no]
            exp_fn[no_sess,j,item_no] = 20 - exp_tp[no_sess,j,item_no]
        
        for j in range(4):
            exp_precision[no_sess,j,item_no] = exp_tp[no_sess,j,item_no] / (exp_tp[no_sess,j,item_no] + exp_fp[no_sess,j,item_no])
            exp_recall_sensitivity[no_sess,j,item_no] = exp_tp[no_sess,j,item_no] / (exp_tp[no_sess,j,item_no] + exp_fn[no_sess,j,item_no])
            exp_specificity[no_sess,j,item_no] = exp_tn[no_sess,j,item_no] / (exp_tn[no_sess,j,item_no] + exp_fp[no_sess,j,item_no])
        
for i in range(4):
    for j in range(4):
        print("Precision: Avg. ± Std. for exp {} val {}: {:.2f}±{:.2f}% ".format(i, j, np.array(exp_precision[i,j]).mean()*100, np.array(exp_precision[i,j]).std()*100))
        #print("Std. for exp {} val {}: {}".format(i, j, np.array(exp_val[i,j]).std()))
    print("\n")
    
print("\n////////////////////\n")
    
for i in range(4):
    for j in range(4):
        print("Recall: Avg. ± Std. for exp {} val {}: {:.2f}±{:.2f}% ".format(i, j, np.array(exp_recall_sensitivity[i,j]).mean()*100, np.array(exp_recall_sensitivity[i,j]).std()*100))
        #print("Std. for exp {} val {}: {}".format(i, j, np.array(exp_val[i,j]).std()))
    print("\n")
        
print("\n////////////////////\n")

for i in range(4):
    for j in range(4):
        print("Specificity: Avg. ± Std. for exp {} val {}: {:.2f}±{:.2f}% ".format(i, j, np.array(exp_specificity[i,j]).mean()*100, np.array(exp_specificity[i,j]).std()*100))
        #print("Std. for exp {} val {}: {}".format(i, j, np.array(exp_val[i,j]).std()))
    print("\n")
        
print("\n////////////////////\n")

Precision: Avg. ± Std. for exp 0 val 0: 100.00±0.00% 
Precision: Avg. ± Std. for exp 0 val 1: 79.07±6.87% 
Precision: Avg. ± Std. for exp 0 val 2: 68.40±3.75% 
Precision: Avg. ± Std. for exp 0 val 3: 63.40±3.86% 


Precision: Avg. ± Std. for exp 1 val 0: 93.58±3.31% 
Precision: Avg. ± Std. for exp 1 val 1: 82.06±6.35% 
Precision: Avg. ± Std. for exp 1 val 2: 89.36±7.49% 
Precision: Avg. ± Std. for exp 1 val 3: 74.59±8.04% 


Precision: Avg. ± Std. for exp 2 val 0: 82.53±9.32% 
Precision: Avg. ± Std. for exp 2 val 1: 74.25±2.25% 
Precision: Avg. ± Std. for exp 2 val 2: 78.68±2.19% 
Precision: Avg. ± Std. for exp 2 val 3: 67.90±5.95% 


Precision: Avg. ± Std. for exp 3 val 0: 94.37±1.73% 
Precision: Avg. ± Std. for exp 3 val 1: 89.40±6.72% 
Precision: Avg. ± Std. for exp 3 val 2: 97.78±4.44% 
Precision: Avg. ± Std. for exp 3 val 3: 76.28±7.88% 



////////////////////

Recall: Avg. ± Std. for exp 0 val 0: 100.00±0.00% 
Recall: Avg. ± Std. for exp 0 val 1: 56.00±9.70% 
Recall: Avg. ± Std.